
loading the model into colab content/
---



In [1]:
# URL from which you're downloading the model
#url = "https://huggingface.co/ssoh/llama-2-7b-mcq_2-GGUF/resolve/main/llama-2-7b-mcq_2.Q5_K_M.gguf" #new
url = "https://huggingface.co/ssoh/llama-2-7b-mini-ibased-GGUF/resolve/main/llama-2-7b-mini-ibased.Q5_K_M.gguf" #old

In [2]:
#step A, load the model into local folder
!wget {url}

--2024-02-22 07:54:45--  https://huggingface.co/ssoh/llama-2-7b-mini-ibased-GGUF/resolve/main/llama-2-7b-mini-ibased.Q5_K_M.gguf
Resolving huggingface.co (huggingface.co)... 13.224.249.43, 13.224.249.10, 13.224.249.119, ...
Connecting to huggingface.co (huggingface.co)|13.224.249.43|:443... connected.
HTTP request sent, awaiting response... 307 Temporary Redirect
Location: /BitBasher/llama-2-7b-mini-ibased-GGUF/resolve/main/llama-2-7b-mini-ibased.Q5_K_M.gguf [following]
--2024-02-22 07:54:45--  https://huggingface.co/BitBasher/llama-2-7b-mini-ibased-GGUF/resolve/main/llama-2-7b-mini-ibased.Q5_K_M.gguf
Reusing existing connection to huggingface.co:443.
HTTP request sent, awaiting response... 302 Found
Location: https://cdn-lfs-us-1.huggingface.co/repos/a7/16/a716a6f7d3f2fa140d2f0263054d2bc120c1eca46172da4411fa02e97e0236bc/1fad558a8c0c265b3f1ef73559d401fdde00a1945e632c8c7523c066002aac4a?response-content-disposition=attachment%3B+filename*%3DUTF-8%27%27llama-2-7b-mini-ibased.Q5_K_M.gguf%3

#Docker functions start from here

---



In [3]:
!pip -q install langchain llama-cpp-python pypdf chromadb sentence-transformers

     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 816.1/816.1 kB 16.4 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 36.7/36.7 MB 35.4 MB/s eta 0:00:00
  Installing build dependencies ... done
  Getting requirements to build wheel ... done
  Installing backend dependencies ... done
  Preparing metadata (pyproject.toml) ... done
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 284.0/284.0 kB 31.9 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 509.0/509.0 kB 47.2 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 132.8/132.8 kB 16.2 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 1.7/1.7 MB 74.4 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 242.1/242.1 kB 29.6 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 61.0/61.0 kB 8.4 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 45.5/45.5 kB 6.2 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 2.4/2.4 MB 82.4 MB/s eta 0:00:00
     ━━━

In [4]:
#list of librarys for requirement.txt
from langchain.document_loaders import PyPDFLoader

# Import embeddings module from langchain for vector representations of text
from langchain.embeddings import HuggingFaceEmbeddings

# Import text splitter for handling large texts
from langchain.text_splitter import CharacterTextSplitter

# Import vector store for database operations
from langchain.vectorstores import Chroma

# for loading of llama gguf model
from langchain.llms import LlamaCpp

from langchain.chains.router.llm_router import LLMRouterChain, RouterOutputParser
from langchain.chains.router.multi_prompt_prompt import MULTI_PROMPT_ROUTER_TEMPLATE

from langchain.memory import VectorStoreRetrieverMemory #new

In [5]:
from langchain.chains.router import MultiPromptChain
from langchain.chains import ConversationChain
from langchain.chains.llm import LLMChain
from langchain.prompts import PromptTemplate
from langchain.memory import ConversationBufferMemory
from langchain.chains import ConversationalRetrievalChain

from langchain.callbacks.manager import CallbackManager
from langchain.callbacks.streaming_stdout import StreamingStdOutCallbackHandler

In [6]:
#Step 1, call this function once to instantiate it, this is to convert pdf into chromadb collection_name has no use for now
def pdf_to_vec(filename):
  document = []
  loader = PyPDFLoader(filename)
  document.extend(loader.load()) #which library is this from?

  # Initialize HuggingFaceEmbeddings with the 'sentence-transformers/all-MiniLM-L6-v2' model for generating text embeddings
  embeddings = HuggingFaceEmbeddings(model_name='sentence-transformers/all-MiniLM-L6-v2')

  # Initialize a CharacterTextSplitter to split the loaded documents into smaller chunks
  document_splitter = CharacterTextSplitter(separator='\n', chunk_size=500, chunk_overlap=100)

  # Use the splitter to divide the 'document' content into manageable chunks
  document_chunks = document_splitter.split_documents(document) #which library is this from?

  # Create a Chroma vector database from the document chunks with the specified embeddings, and set a directory for persistence
  vectordb = Chroma.from_documents(document_chunks, embedding=embeddings, persist_directory='./data') ## change to GUI path

  # Persist the created vector database to disk in the specified directory
  vectordb.persist() #this is mandatory?

  return(vectordb)
  #return collection  # Return the collection as the asset

In [7]:
#step 2 upload the file and return vectordb for langchain
#https://drive.google.com/file/d/1tkX0lNFidzaoK4V1sm1qvkjWkcfZjDuc/view?usp=drive_link

vectordb = pdf_to_vec("DEUSCHLE-SENIORTHESIS-2019.pdf") #filepath to pdf in application

/usr/local/lib/python3.10/dist-packages/huggingface_hub/utils/_token.py:88: UserWarning: 
The secret `HF_TOKEN` does not exist in your Colab secrets.
To authenticate with the Hugging Face Hub, create a token in your settings tab (https://huggingface.co/settings/tokens), set it as secret in your Google Colab and restart your session.
You will be able to reuse this secret in all of your notebooks.
Please note that authentication is recommended but still optional to access public models or datasets.
  warnings.warn(


modules.json:   0%|          | 0.00/349 [00:00<?, ?B/s]

config_sentence_transformers.json:   0%|          | 0.00/116 [00:00<?, ?B/s]

README.md:   0%|          | 0.00/10.7k [00:00<?, ?B/s]

sentence_bert_config.json:   0%|          | 0.00/53.0 [00:00<?, ?B/s]

...

tokenizer_config.json:   0%|          | 0.00/350 [00:00<?, ?B/s]

vocab.txt:   0%|          | 0.00/232k [00:00<?, ?B/s]

tokenizer.json:   0%|          | 0.00/466k [00:00<?, ?B/s]

special_tokens_map.json:   0%|          | 0.00/112 [00:00<?, ?B/s]

1_Pooling/config.json:   0%|          | 0.00/190 [00:00<?, ?B/s]

In [ ]:
#NOT FOR DOCKER APP, this is for development only. for use after session restart, re-instaniate vectordb to created chromadb
embeddings = HuggingFaceEmbeddings(model_name='sentence-transformers/all-MiniLM-L6-v2')
vectordb= Chroma(persist_directory = './data', embedding_function = embeddings)

###chromdb created

---
###Starting function for LLM


In [10]:
#step 3. call once to instanaite the function
#https://python.langchain.com/docs/integrations/llms/llamacpp for CPU usage

def load_llm():
  #callback_manager = CallbackManager([StreamingStdOutCallbackHandler()])
  llm = LlamaCpp(
              #streaming = True,
              model_path="/content/llama-2-7b-mini-ibased.Q5_K_M.gguf",
              n_gpu_layers=-1, # to comment for CPU
              n_batch=512,
              temperature=0.1,
              top_p=1,
              #verbose=False,
              #callback_manager=callback_manager,
              max_tokens=2000,
              )
  return llm

In [11]:
#step 4, to call and load the model once, for repeative usage, the return llm is required for infering function
llm=load_llm()

llama_model_loader: loaded meta data with 24 key-value pairs and 291 tensors from /content/llama-2-7b-mini-ibased.Q5_K_M.gguf (version GGUF V3 (latest))
llama_model_loader: Dumping metadata keys/values. Note: KV overrides do not apply in this output.
llama_model_loader: - kv   0:                       general.architecture str              = llama
llama_model_loader: - kv   1:                               general.name str              = LLaMA v2
llama_model_loader: - kv   2:                       llama.context_length u32              = 4096
llama_model_loader: - kv   3:                     llama.embedding_length u32              = 4096
llama_model_loader: - kv   4:                          llama.block_count u32              = 32
llama_model_loader: - kv   5:                  llama.feed_forward_length u32              = 11008
llama_model_loader: - kv   6:                 llama.rope.dimension_count u32              = 128
llama_model_loader: - kv   7:                 llama.attention.head_

https://github.com/langchain-ai/langchain/issues/5163

In [ ]:
#attempt to resolve MULTI_PROMPT_ROUTER_TEMPLATE class as, LLM output for router chain is not predictable. the class is expecting a standardized json output which LLM may not produce 100% of the time
import json
import langchain
from typing import Any, Dict, List, Optional, Type, cast

class RouterOutputParser_simple(langchain.schema.BaseOutputParser[Dict[str, str]]):
    """Parser for output of router chain int he multi-prompt chain."""

    default_destination: str = "DEFAULT"
    next_inputs_type: Type = str
    next_inputs_inner_key: str = "input"

    def parse(self, text: str) -> Dict[str, Any]:
        try:
            expected_keys = ["destination", "next_inputs"]
            parsed = json.loads(text) ### this line is changed
            if not isinstance(parsed["destination"], str):
                raise ValueError("Expected 'destination' to be a string.")
            if not isinstance(parsed["next_inputs"], self.next_inputs_type):
                raise ValueError(
                    f"Expected 'next_inputs' to be {self.next_inputs_type}."
                )
            parsed["next_inputs"] = {self.next_inputs_inner_key: parsed["next_inputs"]}
            if (
                parsed["destination"].strip().lower()
                == self.default_destination.lower()
            ):
                parsed["destination"] = None
            else:
                parsed["destination"] = parsed["destination"].strip()
            return parsed
        except Exception as e:

            f"Parsing text\n{text}\n raised following error:\n{e}"


In [12]:
#step 5, to instantiate once to create default_chain,router_chain,destination_chains into chain and set vectordb. so will not re-create per prompt
def default_chain():

  sum_template = """
  As a machine learning education specialist, your expertise is pivotal in deepening the comprehension of complex machine learning concepts for both educators and students.

  Your role entails:

  Providing Detailed Explanations: Deliver comprehensive answers to these questions, elucidating the underlying technical principles.
  Assisting in Exam Preparation: Support educators in formulating sophisticated exam and quiz questions, including MCQs, accompanied by thorough explanations.
  Summarizing Course Material: Distill key information from course materials, articulating complex ideas within the context of advanced machine learning practices.

  Objective: to summarize and explain the key points.
  summary:

  Here the question:
  {input}
  """

  mcq_template = """
  As a machine learning education specialist, your expertise is pivotal in deepening the comprehension of complex machine learning concepts for both educators and students.

  Your role entails:
  Crafting Insightful Questions: Develop thought-provoking questions that explore the intricacies of machine learning topics.
  Generating MCQs: Create MCQs for each machine learning topic, comprising a question, four choices (A-D), and the correct answer, along with a rationale explaining the answer.

  Objective: to create multiple choice question in this format
  question:
  options A:
  options B:
  options C:
  options D:
  correct_answer:
  explanation:

  Here the question:
  {input}
  """

  prompt_infos = [
      {
          "name": "SUMMARIZE",
          "description": "Good for summarizing and explaination",
          "prompt_template": sum_template,
      },
      {
          "name": "MCQ",
          "description": "Good for creating multiple choices questions mcq",
          "prompt_template": mcq_template,
      },
  ]

  destination_chains = {}

  for p_info in prompt_infos:
    name = p_info["name"]
    prompt_template = p_info["prompt_template"]
    prompt = PromptTemplate(template=prompt_template, input_variables=["input"])
    embeddings = HuggingFaceEmbeddings(model_name='sentence-transformers/all-MiniLM-L6-v2')
    vectordb= Chroma(persist_directory = './data', embedding_function = embeddings)
    retriever = vectordb.as_retriever()
    memory = VectorStoreRetrieverMemory(retriever=retriever)

    chain = LLMChain(llm=llm, prompt=prompt, verbose=True, memory=memory)
    destination_chains[name] = chain

  default_chain = ConversationalRetrievalChain.from_llm(llm=llm,
                                                retriever=vectordb.as_retriever(search_kwargs={'k': 3}),
                                                verbose=True, output_key="text" )

  destinations = [f"{p['name']}: {p['description']}" for p in prompt_infos]
  destinations_str = "\n".join(destinations)
  print(destinations_str)
  router_template = MULTI_PROMPT_ROUTER_TEMPLATE.format(destinations=destinations_str)
  router_prompt = PromptTemplate(
      template=router_template,
      input_variables=["input"],
      output_parser=RouterOutputParser(),
  )
  router_chain = LLMRouterChain.from_llm(llm, router_prompt)
  print("destination_chains:",destination_chains)
  return default_chain,router_chain,destination_chains

In [13]:
#step 6, to instantiate once to create default_chain,router_chain,destination_chains into chain and set vectordb. so will not re-create per prompt

default_chain,router_chain,destination_chains = default_chain()

SUMMARIZE: Good for summarizing and explaination
MCQ: Good for creating multiple choices questions mcq
destination_chains: {'SUMMARIZE': LLMChain(memory=VectorStoreRetrieverMemory(retriever=VectorStoreRetriever(tags=['Chroma', 'HuggingFaceEmbeddings'], vectorstore=<langchain_community.vectorstores.chroma.Chroma object at 0x7b98f6df0040>)), verbose=True, prompt=PromptTemplate(input_variables=['input'], template='\n  As a machine learning education specialist, your expertise is pivotal in deepening the comprehension of complex machine learning concepts for both educators and students.\n\n  Your role entails:\n\n  Providing Detailed Explanations: Deliver comprehensive answers to these questions, elucidating the underlying technical principles.\n  Assisting in Exam Preparation: Support educators in formulating sophisticated exam and quiz questions, including MCQs, accompanied by thorough explanations.\n  Summarizing Course Material: Distill key information from course materials, articulati

In [14]:
#step 7 ,instantiate the function once
def llm_infer(default_chain,router_chain,destination_chains,prompt):

  chain = MultiPromptChain(
      router_chain=router_chain,
      destination_chains=destination_chains,
      default_chain=default_chain,
      #memory=ConversationBufferMemory(k=2), # memory_key='chat_history', return_messages=True
      verbose=True,
  )
  print(prompt)
  response = chain.run(prompt)

  return response

In [18]:
#step 8a call function using this. replace the prompt string with GUI captured prompt
result= llm_infer(default_chain,router_chain,destination_chains,"please give me a mcq on Hidden Markov Models") #input GUI variable

please give me a mcq on Hidden Markov Models


> Entering new MultiPromptChain chain...


/usr/local/lib/python3.10/dist-packages/langchain/chains/llm.py:316: UserWarning: The predict_and_parse method is deprecated, instead pass an output parser directly to LLMChain.
  warnings.warn(
Llama.generate: prefix-match hit

llama_print_timings:        load time =  170049.91 ms
llama_print_timings:      sample time =     114.06 ms /   208 runs   (    0.55 ms per token,  1823.52 tokens per second)
llama_print_timings: prompt eval time =  163286.83 ms /   303 tokens (  538.90 ms per token,     1.86 tokens per second)
llama_print_timings:        eval time =  147224.43 ms /   207 runs   (  711.23 ms per token,     1.41 tokens per second)
llama_print_timings:       total time =  311391.08 ms /   510 tokens
Llama.generate: prefix-match hit


MCQ: {'input': 'please give me a mcq on Hidden Markov Models'}

> Entering new LLMChain chain...
Prompt after formatting:

  As a machine learning education specialist, your expertise is pivotal in deepening the comprehension of complex machine learning concepts for both educators and students.

  Your role entails:
  Crafting Insightful Questions: Develop thought-provoking questions that explore the intricacies of machine learning topics.
  Generating MCQs: Create MCQs for each machine learning topic, comprising a question, four choices (A-D), and the correct answer, along with a rationale explaining the answer.

  Objective: to create multiple choice question in this format
  question:
  options A:
  options B:
  options C:
  options D:
  correct_answer:
  explanation:

  Here the question:
  please give me a mcq on Hidden Markov Models
  



llama_print_timings:        load time =  170049.91 ms
llama_print_timings:      sample time =      98.14 ms /   159 runs   (    0.62 ms per token,  1620.12 tokens per second)
llama_print_timings: prompt eval time =  100196.94 ms /   189 tokens (  530.14 ms per token,     1.89 tokens per second)
llama_print_timings:        eval time =  109954.49 ms /   158 runs   (  695.91 ms per token,     1.44 tokens per second)
llama_print_timings:       total time =  210829.40 ms /   347 tokens



> Finished chain.

> Finished chain.


In [19]:
#for docker to return to GUI
print(result)


  Response:

  question:
  What is the primary difference between a Hidden Markov Model (HMM) and a conventional Markov Model?

  options A: HMM has more states than a conventional Markov Model

  options B: HMM has more transitions than a conventional Markov Model

  options C: HMM has more outputs than a conventional Markov Model

  options D: HMM has more inputs than a conventional Markov Model

  correct_answer: B

  explanation:

  A HMM has more transitions than a conventional Markov Model because an HMM can have multiple states simultaneously, whereas a conventional Markov Model can only be in one state at a time.


In [20]:
#step 8b call function using this. replace the prompt string with GUI captured prompt
result= llm_infer(default_chain,router_chain,destination_chains,"please give me a summary Hidden Markov Models") #input GUI variable

please give me a summary Hidden Markov Models


> Entering new MultiPromptChain chain...


/usr/local/lib/python3.10/dist-packages/langchain/chains/llm.py:316: UserWarning: The predict_and_parse method is deprecated, instead pass an output parser directly to LLMChain.
  warnings.warn(
Llama.generate: prefix-match hit

llama_print_timings:        load time =  170049.91 ms
llama_print_timings:      sample time =     108.70 ms /   191 runs   (    0.57 ms per token,  1757.08 tokens per second)
llama_print_timings: prompt eval time =  159612.33 ms /   300 tokens (  532.04 ms per token,     1.88 tokens per second)
llama_print_timings:        eval time =  137167.79 ms /   190 runs   (  721.94 ms per token,     1.39 tokens per second)
llama_print_timings:       total time =  297613.67 ms /   490 tokens
Llama.generate: prefix-match hit


SUMMARIZE: {'input': 'please give me a summary Hidden Markov Models'}

> Entering new LLMChain chain...
Prompt after formatting:

  As a machine learning education specialist, your expertise is pivotal in deepening the comprehension of complex machine learning concepts for both educators and students.

  Your role entails:

  Providing Detailed Explanations: Deliver comprehensive answers to these questions, elucidating the underlying technical principles.
  Assisting in Exam Preparation: Support educators in formulating sophisticated exam and quiz questions, including MCQs, accompanied by thorough explanations.
  Summarizing Course Material: Distill key information from course materials, articulating complex ideas within the context of advanced machine learning practices.

  Objective: to summarize and explain the key points.
  summary:

  Here the question:
  please give me a summary Hidden Markov Models
  



llama_print_timings:        load time =  170049.91 ms
llama_print_timings:      sample time =     199.50 ms /   328 runs   (    0.61 ms per token,  1644.09 tokens per second)
llama_print_timings: prompt eval time =   96984.80 ms /   183 tokens (  529.97 ms per token,     1.89 tokens per second)
llama_print_timings:        eval time =  230166.40 ms /   327 runs   (  703.87 ms per token,     1.42 tokens per second)
llama_print_timings:       total time =  328617.54 ms /   510 tokens



> Finished chain.

> Finished chain.


In [21]:
#for docker to return to GUI
print(result)


  Response:

  Hidden Markov Models (HMMs) are a type of probabilistic model that can be used to represent and analyze sequential data. In an HMM, the underlying system is modeled as a Markov process with unobservable (or hidden) states that generate observable outcomes or observations. The basic idea is that the observations are generated by the underlying states, and the goal is to infer the most likely state sequence that generated the observations.

HMMs have numerous applications in natural language processing, speech recognition, bioinformatics, and other fields where sequential data is prevalent. They can be used for tasks such as speech recognition, natural language processing, and bioinformatics.

The key components of an HMM include:

1. Observation sequence: A sequence of observations generated by the underlying states
2. State sequence: A sequence of hidden states that generate the observations
3. Transition matrix: A matrix that specifies the probability of transitioning 

#END for docker app

---



In [ ]:
print(chain.run("please give me a mcq on Hidden Markov Models with answer and explaination")) #with old gguf
